In [1]:
# We begin by importing the necessary packages.
import numpy as np          # numpy will be useful for general mathematical calculations;
import seaborn as sn        # seaborn will be useful for plotting heatmaps
import pandas as pd         # pandas will be useful if we want to import any external data

# Plotly will be useful to us for making and displaying plots.
import plotly
import plotly.express as px
import plotly.graph_objects as go
from IPython.display import display, HTML
plotly.offline.init_notebook_mode()
display(HTML('<script type="text/javascript" async src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.1/MathJax.js?config=TeX-MML-AM_SVG"></script>'))

PI = np.pi                  # Pretty self-explanatory.
TAU = 2*PI                  # It is sometimes more convenient to measure time in terms of full cycles.

import os
if not os.path.exists("images"):
    os.mkdir("images")

In [2]:
class ODE:
    def __init__(self, N):
        self.state = np.zeros(N, dtype=float)
        self.rate = np.zeros(N, dtype=float)

    def getState(self):
        return np.copy(self.state)
    
class ODESolver:
    def __init__(self, stepSize=0.01):
        self.dt = stepSize

    def setStepSize(self, stepSize):
        self.dt = stepSize

    def getStepSize(self):
        return self.dt
    
class Euler(ODESolver):
    def step(self, other):
        state = np.array(other.getState())
        rate = np.array(other.getRate())
        other.state = state + rate*self.getStepSize()

class EulerRichardson(ODESolver):
    def step(self, other):
        state = np.array(other.getState())
        rate = np.array(other.getRate())

        other.state = state + (1/2)*rate*self.getStepSize()
        rate = other.getRate()

        other.state = state + rate*self.getStepSize()

class RungeKutta(ODESolver):
    def step(self, other):
        state0 = np.array(other.getState())
        rate0 = np.array(other.getRate())

        other.state = state0 + (1/2)*rate0*self.getStepSize()
        rate1 = np.array(other.getRate())

        other.state = state0 + (1/2)*rate1*self.getStepSize()
        rate2 = np.array(other.getRate())

        other.state = state0 + rate2*self.getStepSize()
        rate3 = np.array(other.getRate())

        other.state = state0 + (1/6)*(rate0 + 2*rate1 + 2*rate2 + rate3)*self.getStepSize()

In [3]:
class Needle(ODE):
    def __init__(self, phi0, phiDot0, t0=0, gamma=0, omega0=0, lam=0, omega=0):
        super().__init__(3)
        self.state[0] = phi0
        self.state[1] = phiDot0
        self.state[2] = t0

        self.phiList = [phi0]
        self.phiDotList = [phiDot0]
        self.tList = [t0]
        self.history = [self.phiList, self.phiDotList, self.tList]

        self.gamma = gamma
        self.omega0 = omega0
        self.lam = lam
        self.omega = omega

    def getRate(self):
        self.rate[0] = self.state[1]
        self.rate[1] = -self.gamma*self.state[1] - np.sin(self.state[0])*(self.omega0**2 + np.cos(self.omega*self.state[2])*(1/2)*(self.lam**2 * self.omega**2))
        self.rate[2] = 1
        return self.rate
    
    def solveODE(self, T):
        solver = RungeKutta()

        while self.state[-1] < T:
            solver.step(self)

            if self.state[0] > PI:
                self.state[0] -= 2*PI
            elif self.state[0] <= -PI:
                self.state[0] += 2*PI

            for n in range(len(self.state)):
                self.history[n].append(self.state[n])

    def plotPhaseSpace(self, nTransient=0, step=1, color=False):
        df = pd.DataFrame()
        df['phi'] = self.history[0][nTransient::step]
        df['phiDot'] = self.history[1][nTransient::step]
        df['time'] = self.history[2][nTransient::step]

        if color:
            fig = px.scatter(df, x='phi', y='phiDot', color='time', width=500, height=400)
        else:
            fig = px.scatter(df, x='phi', y='phiDot', width=500, height=400)

        fig.update_layout(xaxis_title=r'$\phi$', yaxis_title=r'$\dot \phi$', margin=dict(l=20, r=20, t=20, b=20))
        fig.show()

    def plotPoincareMap(self, nTransient=0, color=False):
        if self.omega > 0:
            fieldStep = int((2*PI/self.omega)/(0.01))
            self.plotPhaseSpace(nTransient, fieldStep, color=color)

    def plotTrajectory(self):
        df = pd.DataFrame()
        df['phi'] = self.history[0]
        df['time'] = self.history[2]
        fig = px.line(df, x="time", y="phi")
        fig.update_layout(xaxis_title=r'$t$', yaxis_title=r'$\phi$', margin=dict(l=20, r=20, t=20, b=20))
        fig.show()

In [35]:
n1 = Needle(phi0=PI/4, phiDot0=0, t0=0, gamma=0.05, omega0=0, lam=2, omega=4*PI)
n1.solveODE(T=50*TAU)
n1.plotPoincareMap(color=True)
n1.plotTrajectory()